In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt
import optuna
import seaborn as sns
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import MinMaxScaler
from lightgbm import early_stopping
from lightgbm import log_evaluation

In [2]:
#Cell_2.
df_train = pd.read_csv('data/train.csv')
df_test = pd.read_csv('data/test.csv')
print(df_train.shape)
print(df_train.info())
display(df_train.head())

(891, 12)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB
None


PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [3]:
#Cell_3.
print(df_test.shape)
print(df_test.info())
display(df_test.head())

(418, 11)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pclass       418 non-null    int64  
 2   Name         418 non-null    object 
 3   Sex          418 non-null    object 
 4   Age          332 non-null    float64
 5   SibSp        418 non-null    int64  
 6   Parch        418 non-null    int64  
 7   Ticket       418 non-null    object 
 8   Fare         417 non-null    float64
 9   Cabin        91 non-null     object 
 10  Embarked     418 non-null    object 
dtypes: float64(2), int64(4), object(5)
memory usage: 36.0+ KB
None


PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  34.5      0      0   330911   7.8292   NaN        Q  
1  47.0      1      0   363272   7.0000   NaN        S  
2  62.0      0      0   240276   9.6875   NaN        Q  
3  27.0      0      0   315154   8.6625   NaN        S  
4  22.0      1      1  3101298  12.2875   NaN        S

In [4]:
#Cell_4.
df_train2 = df_train.drop(['PassengerId', 'Name', 'Ticket','Cabin'],axis=1)
df_test2 = df_test.drop(['PassengerId', 'Name', 'Ticket','Cabin'],axis=1)
display(df_train2.head())
display(df_test2.head())

Survived  Pclass     Sex   Age  SibSp  Parch     Fare Embarked
0         0       3    male  22.0      1      0   7.2500        S
1         1       1  female  38.0      1      0  71.2833        C
2         1       3  female  26.0      0      0   7.9250        S
3         1       1  female  35.0      1      0  53.1000        S
4         0       3    male  35.0      0      0   8.0500        S

Pclass     Sex   Age  SibSp  Parch     Fare Embarked
0       3    male  34.5      0      0   7.8292        Q
1       3  female  47.0      1      0   7.0000        S
2       2    male  62.0      0      0   9.6875        Q
3       3    male  27.0      0      0   8.6625        S
4       3  female  22.0      1      1  12.2875        S

In [5]:
#Cell_7.
#merging train and test datasets.
df_test['Survived']=2
df_merged=pd.concat([df_train,df_test],ignore_index=True)
print(df_merged.shape)
display(df_merged.head())

(1309, 12)


PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [6]:
#Cell_8.
df_merged2 = df_merged.drop(['PassengerId', 'Name', 'Ticket','Cabin'],axis=1)
display(df_merged2.head())
df_merged2.info()

Survived  Pclass     Sex   Age  SibSp  Parch     Fare Embarked
0         0       3    male  22.0      1      0   7.2500        S
1         1       1  female  38.0      1      0  71.2833        C
2         1       3  female  26.0      0      0   7.9250        S
3         1       1  female  35.0      1      0  53.1000        S
4         0       3    male  35.0      0      0   8.0500        S

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1309 entries, 0 to 1308
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Survived  1309 non-null   int64  
 1   Pclass    1309 non-null   int64  
 2   Sex       1309 non-null   object 
 3   Age       1046 non-null   float64
 4   SibSp     1309 non-null   int64  
 5   Parch     1309 non-null   int64  
 6   Fare      1308 non-null   float64
 7   Embarked  1307 non-null   object 
dtypes: float64(2), int64(4), object(2)
memory usage: 81.9+ KB


In [7]:
#Cell_9.
df_merged2['Embarked']=df_merged2['Embarked'].replace({
    'C':3,'Q':2,'S':1
})

C:\Users\rui20\AppData\Local\Temp\ipykernel_3080\1793718829.py:2: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_merged2['Embarked']=df_merged2['Embarked'].replace({


In [8]:
#Cell_11.
df_merged3 = pd.get_dummies(df_merged2,drop_first=True, dtype='uint8')
display(df_merged3.head())
display(df_merged3.tail())

Survived  Pclass   Age  SibSp  Parch     Fare  Embarked  Sex_male
0         0       3  22.0      1      0   7.2500       1.0         1
1         1       1  38.0      1      0  71.2833       3.0         0
2         1       3  26.0      0      0   7.9250       1.0         0
3         1       1  35.0      1      0  53.1000       1.0         0
4         0       3  35.0      0      0   8.0500       1.0         1

Survived  Pclass   Age  SibSp  Parch      Fare  Embarked  Sex_male
1304         2       3   NaN      0      0    8.0500       1.0         1
1305         2       1  39.0      0      0  108.9000       3.0         0
1306         2       3  38.5      0      0    7.2500       1.0         1
1307         2       3   NaN      0      0    8.0500       1.0         1
1308         2       3   NaN      1      1   22.3583       3.0         1

In [9]:
#Cell_12.
mu=df_merged3.mean(numeric_only=True)
print(mu)
df_merged4=df_merged3.fillna(mu)
print(df_merged4.shape)
print(df_merged4.info())

Survived     0.899924
Pclass       2.294882
Age         29.881138
SibSp        0.498854
Parch        0.385027
Fare        33.295479
Embarked     1.507269
Sex_male     0.644003
dtype: float64
(1309, 8)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1309 entries, 0 to 1308
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Survived  1309 non-null   int64  
 1   Pclass    1309 non-null   int64  
 2   Age       1309 non-null   float64
 3   SibSp     1309 non-null   int64  
 4   Parch     1309 non-null   int64  
 5   Fare      1309 non-null   float64
 6   Embarked  1309 non-null   float64
 7   Sex_male  1309 non-null   uint8  
dtypes: float64(3), int64(4), uint8(1)
memory usage: 73.0 KB
None


In [10]:
#Cell_13.
df_train4=df_merged4[df_merged4['Survived']!=2]
display(df_train4.head())

Survived  Pclass   Age  SibSp  Parch     Fare  Embarked  Sex_male
0         0       3  22.0      1      0   7.2500       1.0         1
1         1       1  38.0      1      0  71.2833       3.0         0
2         1       3  26.0      0      0   7.9250       1.0         0
3         1       1  35.0      1      0  53.1000       1.0         0
4         0       3  35.0      0      0   8.0500       1.0         1

In [11]:
#Cell_14.
y=df_train4['Survived']
X=df_train4.iloc[:,1:]
print(X.head())

   Pclass   Age  SibSp  Parch     Fare  Embarked  Sex_male
0       3  22.0      1      0   7.2500       1.0         1
1       1  38.0      1      0  71.2833       3.0         0
2       3  26.0      0      0   7.9250       1.0         0
3       1  35.0      1      0  53.1000       1.0         0
4       3  35.0      0      0   8.0500       1.0         1


In [12]:
def objective(trial):
    params = {
        'objective': 'binary',
        'metric': 'binary_logloss',
        'num_leaves': trial.suggest_int('num_leaves', 2, 256),
        'learning_rate': trial.suggest_float('learning_rate', 1e-8, 1.0, log=True),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.4, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.4, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 7),      
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0, log=True),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0, log=True),
        'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
    }

    X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, stratify=y)
    
    sc = MinMaxScaler(feature_range=(0, 1), copy=True)
    sc.fit(X_train)
    X_train_std = sc.transform(X_train)
    
    train_data = lgb.Dataset(X_train_std, label=y_train)
    val_data = lgb.Dataset(X_val, label=y_val)

    callbacks = [
        early_stopping(stopping_rounds=100),
        log_evaluation(period=0)  # verbose_eval=Falseと同等
    ]
    
    model = lgb.train(params, train_data, num_boost_round=1000,
                      valid_sets=[val_data], callbacks=callbacks)
    
    
    preds_proba = model.predict(X_val)
    # 確率をクラスラベルに変換（0.5をしきい値として使用）
    preds_class = (preds_proba > 0.5).astype(int)
    
    accuracy = accuracy_score(y_val, preds_class)
    return accuracy

study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)

[I 2024-07-01 10:20:04,296] A new study created in memory with name: no-name-d0b5e9d1-89d8-48bd-95e1-3acb97405e7c


[LightGBM] [Info] Number of positive: 273, number of negative: 439
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000628 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 198
[LightGBM] [Info] Number of data points in the train set: 712, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.383427 -> initscore=-0.475028
[LightGBM] [Info] Start training from score -0.475028
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[L

[I 2024-07-01 10:20:05,746] Trial 0 finished with value: 0.6145251396648045 and parameters: {'num_leaves': 98, 'learning_rate': 4.6469190781594145e-06, 'feature_fraction': 0.4425694614448977, 'bagging_fraction': 0.8368705840437429, 'bagging_freq': 1, 'lambda_l1': 1.0168232680288187, 'lambda_l2': 0.07623437224334438, 'min_child_samples': 94}. Best is trial 0 with value: 0.6145251396648045.


[LightGBM] [Info] Number of positive: 273, number of negative: 439
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000506 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 206
[LightGBM] [Info] Number of data points in the train set: 712, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.383427 -> initscore=-0.475028
[LightGBM] [Info] Start training from score -0.475028
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [W

[I 2024-07-01 10:20:07,747] Trial 1 finished with value: 0.6145251396648045 and parameters: {'num_leaves': 116, 'learning_rate': 3.251277484020144e-08, 'feature_fraction': 0.8530241509977268, 'bagging_fraction': 0.5391441829595145, 'bagging_freq': 1, 'lambda_l1': 1.2012694620306261e-07, 'lambda_l2': 1.1234463100817271, 'min_child_samples': 19}. Best is trial 0 with value: 0.6145251396648045.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-07-01 10:22:00,230] Trial 98 finished with value: 0.8156424581005587 and parameters: {'num_leaves': 25, 'learning_rate': 0.3477562767915973, 'feature_fraction': 0.6145015676323191, 'bagging_fraction': 0.8505906390186111, 'bagging_freq': 7, 'lambda_l1': 6.095653159521226, 'lambda_l2': 0.00010416163593685234, 'min_child_samples': 86}. Best is trial 31 with value: 0.8324022346368715.


[LightGBM] [Info] Number of positive: 273, number of negative: 439
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000485 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 199
[LightGBM] [Info] Number of data points in the train set: 712, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.383427 -> initscore=-0.475028
[LightGBM] [Info] Start training from score -0.475028
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [W

[I 2024-07-01 10:22:00,424] Trial 99 finished with value: 0.7877094972067039 and parameters: {'num_leaves': 11, 'learning_rate': 0.37385010848173034, 'feature_fraction': 0.7665466476764354, 'bagging_fraction': 0.9000835305455245, 'bagging_freq': 7, 'lambda_l1': 6.889779920355427, 'lambda_l2': 0.000269810980525497, 'min_child_samples': 87}. Best is trial 31 with value: 0.8324022346368715.


[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.383427 -> initscore=-0.475028
[LightGBM] [Info] Start training from score -0.475028
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Training until validation scores don't improve for 100 rounds
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive g

In [13]:
print('Best trial:')
trial = study.best_trial
print('  Value: {}'.format(trial.value))
print('  Params: ')
for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

Best trial:
  Value: 0.8324022346368715
  Params: 
    num_leaves: 110
    learning_rate: 0.034490240644932564
    feature_fraction: 0.49832610485327977
    bagging_fraction: 0.9938601747985935
    bagging_freq: 6
    lambda_l1: 1.4749902544709672
    lambda_l2: 1.8595716327240312e-06
    min_child_samples: 100


In [14]:
best_params = study.best_params

best_model = lgb.LGBMClassifier(**best_params)
best_model.fit(X, y)

[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lambda_l2 is set=1.8595716327240312e-06, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.8595716327240312e-06
[LightGBM] [Warning] bagging_fraction is set=0.9938601747985935, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9938601747985935
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lamb

C:\Users\rui20\miniconda3\envs\ds2024\lib\site-packages\joblib\externals\loky\backend\context.py:136: UserWarning: Could not find the number of physical cores for the following reason:
found 0 physical cores < 1
Returning the number of logical cores instead. You can silence this warning by setting LOKY_MAX_CPU_COUNT to the number of cores you want to use.
  warnings.warn(
  File "C:\Users\rui20\miniconda3\envs\ds2024\lib\site-packages\joblib\externals\loky\backend\context.py", line 282, in _count_physical_cores
    raise ValueError(f"found {cpu_count_physical} physical cores < 1")


LGBMClassifier(bagging_fraction=0.9938601747985935, bagging_freq=6,
               feature_fraction=0.49832610485327977,
               lambda_l1=1.4749902544709672, lambda_l2=1.8595716327240312e-06,
               learning_rate=0.034490240644932564, min_child_samples=100,
               num_leaves=110)

In [27]:
test = df_test.drop(columns=["Name","PassengerId", "Ticket", "Cabin", "Survived"])

In [28]:
test['Embarked']=test['Embarked'].replace(
{
    'C':3,'Q':2,'S':1
}
)
test2 = pd.get_dummies(test,drop_first=True, dtype='uint8')
mu=test2.mean(numeric_only=True)
test3=test2.fillna(mu)
test3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Pclass    418 non-null    int64  
 1   Age       418 non-null    float64
 2   SibSp     418 non-null    int64  
 3   Parch     418 non-null    int64  
 4   Fare      418 non-null    float64
 5   Embarked  418 non-null    int64  
 6   Sex_male  418 non-null    uint8  
dtypes: float64(2), int64(4), uint8(1)
memory usage: 20.1 KB


C:\Users\rui20\AppData\Local\Temp\ipykernel_3080\1613109551.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  test['Embarked']=test['Embarked'].replace(


In [17]:
display(X.head())
display(test3.head())

Pclass   Age  SibSp  Parch     Fare  Embarked  Sex_male
0       3  22.0      1      0   7.2500       1.0         1
1       1  38.0      1      0  71.2833       3.0         0
2       3  26.0      0      0   7.9250       1.0         0
3       1  35.0      1      0  53.1000       1.0         0
4       3  35.0      0      0   8.0500       1.0         1

Pclass   Age  SibSp  Parch     Fare  Embarked  Sex_male
0       3  34.5      0      0   7.8292         2         1
1       3  47.0      1      0   7.0000         1         0
2       2  62.0      0      0   9.6875         2         1
3       3  27.0      0      0   8.6625         1         1
4       3  22.0      1      1  12.2875         1         0

In [18]:
sc = MinMaxScaler(feature_range=(0, 1), copy=True)
sc.fit(X)
train_std = sc.transform(X)
display(train_std)
sc.fit(test3)
test_std = sc.transform(test3)
display(test_std)

array([[1.        , 0.27117366, 0.125     , ..., 0.01415106, 0.        ,
        1.        ],
       [0.        , 0.4722292 , 0.125     , ..., 0.13913574, 1.        ,
        0.        ],
       [1.        , 0.32143755, 0.        , ..., 0.01546857, 0.        ,
        0.        ],
       ...,
       [1.        , 0.37020781, 0.125     , ..., 0.04577135, 0.        ,
        0.        ],
       [0.        , 0.32143755, 0.        , ..., 0.0585561 , 1.        ,
        1.        ],
       [1.        , 0.39683338, 0.        , ..., 0.01512699, 0.5       ,
        1.        ]])

array([[1.        , 0.4527232 , 0.        , ..., 0.01528158, 0.5       ,
        1.        ],
       [1.        , 0.61756561, 0.125     , ..., 0.01366309, 0.        ,
        0.        ],
       [0.5       , 0.8153765 , 0.        , ..., 0.01890874, 0.5       ,
        1.        ],
       ...,
       [1.        , 0.50547277, 0.        , ..., 0.01415106, 0.        ,
        1.        ],
       [1.        , 0.39697468, 0.        , ..., 0.01571255, 0.        ,
        1.        ],
       [1.        , 0.39697468, 0.125     , ..., 0.0436405 , 1.        ,
        1.        ]])

In [29]:
y_pred_train = best_model.predict(train_std)
y_pred_proba_train = best_model.predict_proba(train_std)
accuracy_score(y_pred_train, y)

[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lambda_l2 is set=1.8595716327240312e-06, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.8595716327240312e-06
[LightGBM] [Warning] bagging_fraction is set=0.9938601747985935, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9938601747985935
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lamb

0.7867564534231201

In [30]:
y_pred = best_model.predict(test_std)
y_pred_proba = best_model.predict_proba(test_std)
print(y_pred)

[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lambda_l2 is set=1.8595716327240312e-06, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.8595716327240312e-06
[LightGBM] [Warning] bagging_fraction is set=0.9938601747985935, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9938601747985935
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.49832610485327977, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.49832610485327977
[LightGBM] [Warning] lambda_l1 is set=1.4749902544709672, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.4749902544709672
[LightGBM] [Warning] lamb

In [31]:
df_test["Survived"] = y_pred

In [32]:
submit = df_test[["PassengerId", "Survived"]]

In [33]:
submit

PassengerId  Survived
0            892         0
1            893         1
2            894         0
3            895         0
4            896         1
..           ...       ...
413         1305         0
414         1306         1
415         1307         0
416         1308         0
417         1309         0

[418 rows x 2 columns]

In [39]:
# submit.to_csv('submission_lightGBM-3.csv', index=False)

In [37]:
prev = pd.read_csv("submission_lightGBM-2.csv")
prev

PassengerId  Survived
0            892         0
1            893         0
2            894         0
3            895         1
4            896         1
..           ...       ...
413         1305         0
414         1306         1
415         1307         0
416         1308         0
417         1309         0

[418 rows x 2 columns]

In [38]:
accuracy_score(prev["Survived"], submit["Survived"])

0.7894736842105263